In [14]:
from ngsolve import *
from ngsolve.webgui import Draw
from netgen.occ import *

In [15]:
def solve_lin_system(a,f,gfu,inverse=""):
    aSinv = a.mat.Inverse(gfu.space.FreeDofs(coupling=a.condense),inverse=inverse)
    if a.condense:
        ainv = ((IdentityMatrix(a.mat.height) + a.harmonic_extension) @ (aSinv + a.inner_solve) @ (IdentityMatrix(a.mat.height) + a.harmonic_extension_trans))        
    else:
        ainv = aSinv
    rhs = f.vec.CreateVector()
    rhs.data = f.vec - a.mat * gfu.vec
    gfu.vec.data += ainv * rhs

In [16]:
cyl = Cylinder((0,0,0), Z, h=0.5,r=1)
cyl.faces[0].name="side"
cyl.faces[1].name="top"
cyl.faces[2].name="bottom"
mesh = Mesh(OCCGeometry(cyl).GenerateMesh(maxh=0.3)).Curve(3)
# Draw(mesh);

In [17]:
order = 3

VT1 = HDiv(mesh,order=order, dirichlet="top|bottom|side")
VT2 = HDiv(mesh,order=order, dirichlet="top|bottom|side", hodivfree = True )
VT3 = HDiv(mesh,order=order, dirichlet="top|bottom|side", highest_order_dc=True)
VT4 = HDiv(mesh,order=order, dirichlet="top|bottom|side", hodivfree = True, highest_order_dc=True)
Vhat1 = TangentialFacetFESpace(mesh,order=order, dirichlet="bottom|top")
Vhat2 = Compress(TangentialFacetFESpace(mesh,order=order, dirichlet="bottom|top", highest_order_dc=True, hide_highest_order_dc=True))
Q1 = L2(mesh,order=order-1, lowest_order_wb=True)
Q2 = L2(mesh,order=0, lowest_order_wb=True)
N = NumberSpace(mesh)
fes_params= [(VT1,Vhat1,Q1,"std"), \
             (VT1,Vhat2,Q1,"t. red."), \
             (VT3,Vhat1,Q1,"n. red."), \
             (VT3,Vhat2,Q1,"n.+t. red."), \
             (VT2,Vhat1,Q2,"            hodf"), \
             (VT2,Vhat2,Q2,"t. red.,    hodf"), \
             (VT4,Vhat1,Q2,"n. red.,    hodf"), \
             (VT4,Vhat2,Q2,"n.+t. red., hodf")]
labeled_fes = [(VT * Vhat * Q * N, name) for VT,Vhat,Q,name in fes_params]

In [18]:
def setup_Stokes_HDG_system(fes, **opts):
    nu = 1
    gamma = 10
    yh, zh = fes.TnT()
    order = fes.components[0].globalorder
    (u, uhat, p, lam), (v, vhat, q, mu) = yh, zh
    uh, vh = (u, uhat), (v, vhat)
    tang = lambda u: u - (u*n)*n
    tjump = lambda uh: tang(uh[0]-uh[1]) 

    n = specialcf.normal(mesh.dim)
    h = specialcf.mesh_size

    K = BilinearForm(fes, **opts)
    K += (nu*InnerProduct(Grad(u), Grad(v)) + div(u)*q + div(v)*p + p * mu + q * lam) * dx
    K += nu * Grad(u) * n * tjump(vh) * dx(element_boundary = True)
    K += nu * Grad(v) * n * tjump(uh) * dx(element_boundary = True)
    K += nu  *gamma*order**2/h * InnerProduct ( tjump(vh),  tjump(uh) ) * dx(element_boundary = True)
    K.Assemble()

    r = sqrt(x**2+y**2)
    f = LinearForm(fes)
    f += 500*CF((0,0,r-0.5))*v*dx
    f.Assemble()

    fes.components[0].Average(f.vec)

    return K,f


In [19]:
def draw_solution(gfu):
     N = 15
     points = [ (sin(2*pi*k/N)*i/N, cos(2*pi*k/N)*i/N, j/N)   for i in range(1,N) for j in range(1,N) for k in range(0,N)]
     fl = gfu.components[0]._BuildFieldLines(mesh, points, num_fieldlines=N**3//20, randomized=True, length=1)
     ea = { "euler_angles" : (-40, 0, 0) }
     Draw(gfu.components[0], mesh,  "X", draw_vol=False, draw_surf=True, objects=[fl], \
          min=0, max=1, autoscale=False, settings={"Objects": {"Surface": False, "Wireframe":False}}, **ea);

In [20]:
linsys_opts = [({"condense": True}," local")]
import time
try:
  import pandas as pd
  from IPython.display import display, HTML
  html_output = True
except:
  html_output = False
data = []
with TaskManager():
  for opts, elims in linsys_opts:
    if not html_output:
      print(f"\n\n dof elimination: {elims:9} \n")
      print(f"                |           ndofs          | ncdofs |     nze  | timing (ass.+sol.)")
      print(f"----------------|--------------------------|--------|----------|-------------------")    
    for fes, label in labeled_fes:
      gfu = GridFunction(fes)
      gfu.components[1].Set(CF((y,-x,0)), definedon=mesh.Boundaries("bottom"))
      timer1 = time.time()
      a,f = setup_Stokes_HDG_system(fes, **opts)
      timer2 = time.time()
      solve_lin_system(a,f, gfu=gfu)
      timer3 = time.time()
      if html_output:
        data.append([elims,label,fes.ndof,fes.components[0].ndof,fes.components[1].ndof,
                     fes.components[2].ndof,fes.components[3].ndof,
                     sum(fes.FreeDofs(coupling=True)),
                     "{:.0f}K".format(a.mat.nze/1000),"{:5.3f}".format(timer3-timer1),
                     "{:5.3f}".format(timer2-timer1),"{:5.3f}".format(timer3-timer2)])
      else:
        print(f"{label:16}|",end="")
        print(f"{fes.ndof:5}({fes.components[0].ndof:5}+{fes.components[1].ndof:5}",end="")
        print(f"{fes.components[2].ndof:5}+{fes.components[3].ndof:1})",end=" ")
        print(f"|{sum(fes.FreeDofs(coupling=True)):7}", end=" ")
        print(f"|{a.mat.nze:9}", end=" ")
        print(f"| {timer3-timer1:4.2f} = {timer2-timer1:4.2f} + {timer3-timer2:4.2f}")
      draw_solution(gfu)
if not html_output:
  print(f"----------------|--------------------------|--------|----------|-------------------")
  print("")
else:
  display(HTML(pd.DataFrame(data, 
                            columns=["dof elim.", "FESpace", "ndofs", "nd0", "nd1", 
                                     "nd2", "nd3","ncdofs","nze","time","ass.",
                                     "sol."]).to_html(border=0,index=False)))        



 dof elimination:  local    

                |           ndofs          | ncdofs |     nze  | timing (ass.+sol.)
----------------|--------------------------|--------|----------|-------------------
std             |25501(10980+12040 2480+1) |  13589 |  3316585 | 1.20 = 0.76 + 0.45


WebGuiWidget(layout=Layout(height='500px', width='100%'), value={'gui_settings': {'Objects': {'Surface': False…

t. red.         |20685(10980+ 7224 2480+1) |   9813 |  1802633 | 0.30 = 0.10 + 0.20


WebGuiWidget(layout=Layout(height='500px', width='100%'), value={'gui_settings': {'Objects': {'Surface': False…

n. red.         |27061(12540+12040 2480+1) |  12029 |  2686873 | 0.62 = 0.13 + 0.49


...

n. red.,    hodf|22597(10308+12040  248+1) |  12029 |  2686873 | 0.56 = 0.14 + 0.43


WebGuiWidget(layout=Layout(height='500px', width='100%'), value={'gui_settings': {'Objects': {'Surface': False…

n.+t. red., hodf|17781(10308+ 7224  248+1) |   8253 |  1347641 | 0.38 = 0.19 + 0.18


WebGuiWidget(layout=Layout(height='500px', width='100%'), value={'gui_settings': {'Objects': {'Surface': False…

----------------|--------------------------|--------|----------|-------------------

